In [95]:
import numpy as np
import pandas as pd
import scipy

import json
import re
from itertools import chain
from collections import Counter

In [156]:
with open("./id_all_blip_clusters_12.json") as f:
    d_12 = json.load(f)

with open("./id_all_blip_clusters_24.json") as f:
    d_24 = json.load(f)

with open("./id_all_blip_clusters_48.json") as f:
    d_48 = json.load(f)

In [158]:
def reduce_full_to_ethnicity_model(d):
    c = Counter()
    for k,v in d['labels_full']:
        k_without_gender = re.split("woman|man|person|non-binary",k)
        k_without_gender = ''.join(k_without_gender)
        k_without_gender = k_without_gender.strip().replace("  ", " ")
        c[k_without_gender] = v
    return [[k,v] for k,v in c.items()]

In [142]:
def reduce_full_to_gender_model(d):
    c = Counter()
    for k,v in d['labels_full']:
        k_without_ethnicity = re.split("(woman|man|person|non-binary)", k)
        k_without_ethnicity = ''.join(k_without_ethnicity[1:])
        k_without_ethnicity = k_without_ethnicity.strip().replace("  ", " ")
        c[k_without_ethnicity] = v
    return [[k,v] for k,v in c.items()]

In [154]:
def reduce_full_to_ethnicity_gender(d):
    c = Counter()
    for k,v in d['labels_full']:
        k_without_model = re.split("(woman|man|person|non-binary)", k)
        k_without_model = ''.join(k_without_model[:2])
        k_without_model = k_without_model.strip().replace("  ", " ")
        c[k_without_model] = v
    return [[k,v] for k,v in c.items()]

In [159]:
for cluster_dicts in [d_12, d_24, d_48]:
    for d in cluster_dicts:
        d["labels_ethnicity_model"] = reduce_full_to_ethnicity_model(d)
        d["labels_gender_model"] = reduce_full_to_gender_model(d)
        d["labels_ethnicity_gender"] = reduce_full_to_ethnicity_gender(d)

In [162]:
# p(cluster | ethnicity, model) DONE
# p(cluster | gender, model) DONE
# p(cluster | gender, ethnicity, model) DONE
# p(cluster | ethnicity) DONE
# p(cluster | gender) DONE
# p(cluster | gender, ethnicity) DONE
# p(cluster | model) ADDED, DONE

# Ethnicities

In [74]:
entropies = []
random_entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    random_entropy = dict()
    n_clusters = len(cluster_dicts)
    all_ethnicities = [list(dict(d['labels_ethnicity']).keys()) for d in cluster_dicts]
    all_ethnicities = list(set(chain(*all_ethnicities)))
    for ethnicity in all_ethnicities:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_ethnicity']).get(ethnicity, 0))
        h = np.array(h)
        r = np.ones_like(h)
        entropy[ethnicity] = scipy.stats.entropy(h / sum(h), base=2)
        random_entropy[ethnicity] = scipy.stats.entropy(r, base=2)
    entropies.append(entropy)
    random_entropies.append(random_entropy)

In [79]:
np.log2(48)

5.584962500721156

In [75]:
random_entropy

{'': 5.584962500721156,
 'Latinx': 5.584962500721156,
 'African-American': 5.584962500721156,
 'Hispanic': 5.584962500721156,
 'Indigenous American': 5.584962500721156,
 'First Nations': 5.584962500721156,
 'Black': 5.584962500721156,
 'Multiracial': 5.584962500721156,
 'Latino': 5.584962500721156,
 'Southeast Asian': 5.584962500721156,
 'American Indian': 5.584962500721156,
 'South Asian': 5.584962500721156,
 'Caucasian': 5.584962500721156,
 'Native American': 5.584962500721156,
 'East Asian': 5.584962500721156,
 'Pacific Islander': 5.584962500721156,
 'White': 5.584962500721156}

In [53]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Ethnicities X Model

In [128]:
entropies = []
random_entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    random_entropy = dict()
    n_clusters = len(cluster_dicts)
    all_ethnicities_models = [list(dict(d['labels_ethnicity_model']).keys()) for d in cluster_dicts]
    all_ethnicities_models = list(set(chain(*all_ethnicities_models)))
    for ethnicity_model in all_ethnicities_models:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_ethnicity_model']).get(ethnicity_model, 0))
        h = np.array(h)
        r = np.ones_like(h)
        entropy[ethnicity_model] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [130]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Genders

In [58]:
entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    n_clusters = len(cluster_dicts)
    all_genders = [list(dict(d['labels_gender']).keys()) for d in cluster_dicts]
    all_genders = list(set(chain(*all_genders)))
    for gender in all_genders:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_gender']).get(gender, 0))
        h = np.array(h)
        entropy[gender] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [59]:
entropies

[{'woman': 2.4810719655716675,
  'man': 2.7334846800371837,
  'person': 3.2367086062758728,
  'non-binary': 2.820571495642662},
 {'woman': 3.175925805050219,
  'man': 3.6256634564832084,
  'person': 4.1229292987043635,
  'non-binary': 3.7329829916387802},
 {'woman': 4.424803401742995,
  'man': 4.422651789402228,
  'person': 4.812137497942508,
  'non-binary': 4.421094043509409}]

In [60]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Models

In [84]:
entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    n_clusters = len(cluster_dicts)
    all_models = [list(dict(d['labels_model']).keys()) for d in cluster_dicts]
    all_models = list(set(chain(*all_models)))
    for model in all_models:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_model']).get(model, 0))
        h = np.array(h)
        entropy[model] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [86]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Gender X Model

In [146]:
entropies = []
random_entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    random_entropy = dict()
    n_clusters = len(cluster_dicts)
    all_genders_models = [list(dict(d['labels_gender_model']).keys()) for d in cluster_dicts]
    all_genders_models = list(set(chain(*all_genders_models)))
    for gender_model in all_genders_models:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_gender_model']).get(gender_model, 0))
        h = np.array(h)
        r = np.ones_like(h)
        entropy[gender_model] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [147]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Ethnicity X Gender

In [160]:
entropies = []
random_entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    random_entropy = dict()
    n_clusters = len(cluster_dicts)
    all_ethnicities_genders = [list(dict(d['labels_ethnicity_gender']).keys()) for d in cluster_dicts]
    all_ethnicities_genders = list(set(chain(*all_ethnicities_genders)))
    for ethnicity_gender in all_ethnicities_genders:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_ethnicity_gender']).get(ethnicity_gender, 0))
        h = np.array(h)
        r = np.ones_like(h)
        entropy[ethnicity_gender] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [161]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))

# Genders X Ethnicities X Model

In [66]:
entropies = []
for cluster_dicts in [d_12, d_24, d_48]:
    entropy = dict()
    n_clusters = len(cluster_dicts)
    all_labels = [list(dict(d['labels_full']).keys()) for d in cluster_dicts]
    all_labels = list(set(chain(*all_labels)))
    for label in all_labels:
        h = []
        for i in cluster_dicts:
            h.append(dict(i['labels_full']).get(label, 0))
        h = np.array(h)
        entropy[label] = scipy.stats.entropy(h / sum(h), base=2)
    entropies.append(entropy)

In [67]:
for d in entropies:
    df = pd.DataFrame(pd.Series(d), columns=["entropy"])
    display(df.sort_values("entropy", ascending=False).style.background_gradient(
    axis=None,
    vmin=0,
    vmax=4,
    cmap="YlGnBu"
).format(precision=2))